In [ ]:
# Checkout www.pygimli.org for more examples


# VES inversion for a blocky model

This tutorial shows how an built-in forward operator is used for inversion.
A DC 1D (VES) modelling is used to generate data, noisify and invert them.


We import numpy, matplotlib and the 1D plotting function



In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import pygimli as pg
from pygimli.physics import VESManager

some definitions before (model, data and error)



In [ ]:
#ab2 = np.logspace(-0.5, 2.5, 40)  # AB/2 distance (current electrodes)

define a synthetic model and do a forward simulatin including noise



In [ ]:
#synres = [100., 500., 30.]  # synthetic resistivity
#synthk = [0.5, 3.5]  # synthetic thickness (nlay-th layer is infinite)

the forward operator can be called by f.response(model) or simply f(model)



In [ ]:
#synthModel = synthk + synres  # concatenate thickness and resistivity
#ves = VESManager()
#rhoa, err = ves.simulate(synthModel, ab2=ab2, mn2=0.5,
#                         noiseLevel=0.03, seed=1337)

In [ ]:
# use data from Bausenberg
ab2 = [1.0, 1.25, 1.5, 2.0, 2.5, 3.0, 4.0, 5.0, 6.0, 7.5, 10.0, 12.5, 15.0, 20.0, 25.0, 30.0, 40.0, 50.0, 60.0, 75.0, 100.]
rhoa = [64.0, 70., 77., 89., 103., 115., 152., 179., 206., 244., 305., 360., 410., 489., 540., 588., 672., 605., 535., 433., 283.]
err = np.ones(len(rhoa))*0.02
err[-4:] = 0.05
mn2 = np.ones(len(rhoa))*0.5

In [ ]:
print(ab2)
print(rhoa)
print(err)

In [ ]:
nlay = 3
ves = VESManager()
ves.invert(rhoa, err, ab2=ab2, mn2=mn2,
           nLayers=nlay, lam=1000, lambdaFactor=0.8, cTpye=2, verbose=False)

show estimated & synthetic models and data with model response in 2 subplots



In [ ]:
fig, ax = plt.subplots(ncols=2, figsize=(8, 6))  # two-column figure
#ves.showModel(synthModel, ax=ax[0], label="synth", plot="semilogy", zmax=20)
ves.showModel(ves.model, ax=ax[0], label="model", zmax=50, color="C1")
ves.showData(rhoa, ax=ax[1], label="data", color="C0", marker="o")
out = ves.showData(ves.inv.response, ax=ax[1], label="model", color="C1")

We are interested in the model uncertaincies and through model covariance



In [ ]:
from pygimli.frameworks.resolution import modelCovariance
var, MCM = modelCovariance(ves.inv)
pg.info(var)
fig, ax = plt.subplots()
im = ax.imshow(MCM, vmin=-1, vmax=1, cmap="bwr")
plt.colorbar(im)
labels = [rf'$d_{i+1}$' for i in range(nlay-1)] + \
    [rf'$\rho_{i+1}$' for i in range(nlay)]
plt.xticks(np.arange(nlay*2-1), labels)
_ = plt.yticks(np.arange(nlay*2-1), labels)

The model covariance matrix delivers variances and a scaled (dimensionless)
correlation matrix. The latter show the interdependency of the parameters
among each other. The first and last resistivity is best resolved, also the
first layer thickness. The remaining resistivities and thicknesses are highly
correlated. The variances can be used as error bars in the model plot.



In [ ]:
thk = ves.model[:nlay-1]
res = ves.model[nlay-1:]
z = np.cumsum(thk)
mid = np.hstack([z - thk/2, z[-1]*1.1])
resmean = np.sqrt(res[:-1]*res[1:])
fig, ax = plt.subplots()
#ves.showModel(synthModel, ax=ax, label="synth", plot="semilogy", zmax=20)
ves.showModel(ves.model, ax=ax, label="model", zmax=50)
ax.errorbar(res, mid, marker="*", ls="None", xerr=res*var[nlay-1:])
ax.errorbar(resmean, z, marker="*", ls="None", yerr=thk*var[:nlay-1])

In [ ]:
print(res)
print(res*var[nlay-1:])
print(thk)
print(thk*var[:nlay-1])